In [1]:
import open3d as o3d
import open3d.visualization as viss
import base64
import tempfile
import jpype
import numpy as np
from open3d.cpu.pybind.visualization import MeshColorOption

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
# Enable Java imports
import jpype.imports

# Pull in types
from jpype.types import *

jpype.startJVM(classpath = ['jars/*'])

from org.linkedbuildingdata.ifc2lbd import IFCtoLBDConverter
from org.linkedbuildingdata.ifc2lbd import ConversionProperties
from org.apache.jena.query import QueryFactory, QueryExecutionFactory


In [3]:
# Convert the IFC file into LBD, OPM level 1 model
lbdconverter = IFCtoLBDConverter("https://example.domain.de/",  1)
props = ConversionProperties();
props.setHasGeometry(True);

In [4]:
model=lbdconverter.convert("IFC files\Duplex_A_20110505.ifc",props)

In [5]:
queryString = """PREFIX fog: <https://w3id.org/fog#>
PREFIX beo: <https://pi.pauwel.be/voc/buildingelement#>
PREFIX bot: <https://w3id.org/bot#>
PREFIX ifc: <https://standards.buildingsmart.org/IFC/DEV/IFC2x3/TC1/OWL#>

SELECT ?e ?wkt ?obj WHERE {
  ?e <https://w3id.org/omg#hasGeometry> ?g .
  ?g fog:asObj_v3.0-obj ?obj
  FILTER NOT EXISTS {
    ?e a beo:Window .
  }
  FILTER NOT EXISTS {
    ?e a  bot:Space .
  }
  FILTER NOT EXISTS {
    ?e a   ifc:IfcOpeningElement .
  }


} """

In [6]:
query = QueryFactory.create(queryString)
qexec = QueryExecutionFactory.create(query, model)
results = qexec.execSelect()

In [7]:
while results.hasNext() :
    soln = results.nextSolution()
    x = soln.get("obj")
    print(x)
    base64_bytes = str(x.asLiteral().getLexicalForm()).encode("ascii")
    decoded_bytes = base64.b64decode(base64_bytes)
    decoded_string = decoded_bytes.decode("ascii")
    print(decoded_string)

    virtual_file = tempfile.NamedTemporaryFile(suffix='.obj',mode='w',delete=False)
    print(virtual_file.name)

    virtual_file.write(decoded_string)
    virtual_file.close()

    try:
        mesh = mesh + o3d.io.read_triangle_mesh(virtual_file.name,True,True)
    except NameError:
        mesh = o3d.io.read_triangle_mesh(virtual_file.name,True,True)


diA3LjM2ODU5OTk5OTk5OTk4NSAtMTEuODI1MDAwMDAwMDAwMDAxIDAuMAp2IDcuNDE4NTk5OTk5OTk5OTg0NSAtMTEuODI1MDAwMDAwMDAwMDAxIDAuMAp2IDcuMzY4NTk5OTk5OTk5OTg1IC0xMS40ODk4NDk2Mzg1NTYxNzUgMC4wCnYgNy40MTg1OTk5OTk5OTk5ODQ1IC0xMS40ODk4NDk2Mzg1NTYxNzUgMC4wCnYgNy4zNjg1OTk5OTk5OTk5ODUgLTExLjQ4OTg0OTYzODU1NjE3NSAwLjAKdiA3LjQxODU5OTk5OTk5OTk4NDUgLTExLjQ4OTg0OTYzODU1NjE3NSAwLjAKdiA3LjM2ODU5OTk5OTk5OTk4NSAtOC4wNzUwMDAwMDAwMDAwMDEgMi42NDY1MDg0Njk4ODEyMDIzCnYgNy40MTg1OTk5OTk5OTk5ODQ1IC04LjA3NTAwMDAwMDAwMDAwMSAyLjY0NjUwODQ2OTg4MTIwMjMKdiA3LjM2ODU5OTk5OTk5OTk4NSAtOC4wNzUwMDAwMDAwMDAwMDEgMi42NDY1MDg0Njk4ODEyMDIzCnYgNy40MTg1OTk5OTk5OTk5ODQ1IC04LjA3NTAwMDAwMDAwMDAwMSAyLjY0NjUwODQ2OTg4MTIwMjMKdiA3LjM2ODU5OTk5OTk5OTk4NSAtOC4wNzUwMDAwMDAwMDAwMDEgMy4xMDAwMDAwMDAwMDAxOTYKdiA3LjQxODU5OTk5OTk5OTk4NDUgLTguMDc1MDAwMDAwMDAwMDAxIDMuMTAwMDAwMDAwMDAwMTk2CnYgNy4zNjg1OTk5OTk5OTk5ODUgLTguMDc1MDAwMDAwMDAwMDAxIDMuMTAwMDAwMDAwMDAwMTk2CnYgNy40MTg1OTk5OTk5OTk5ODQ1IC04LjA3NTAwMDAwMDAwMDAwMSAzLjEwMDAwMDAwMDAwMDE5Ngp2IDcuMzY4NTk5OTk5OTk5OTg1

In [8]:
R = np.array([[1, 0, 0], [0, 0, 1], [0, 1, 0]])
mesh.rotate(R, center=(0, 0, 0)) # Switch y an z

mesh.paint_uniform_color([1, 0.5, 0.5])
mesh.compute_vertex_normals()

TriangleMesh with 49944 points and 28516 triangles.

In [9]:
mat_mesh = viss.rendering.MaterialRecord()
mat_mesh.shader = 'defaultLit'
mat_mesh.base_color = [1, 0.8, 0.8, 0.5]
geoms = [{'name': 'mesh', 'geometry': mesh, 'material': mat_mesh}]
viss.draw(geoms)
jpype.shutdownJVM()

[Open3D INFO] Window window_0 created.
[Open3D INFO] ICE servers: {"stun:stun.l.google.com:19302", "turn:user:password@34.69.27.100:3478", "turn:user:password@34.69.27.100:3478?transport=tcp"}
[Open3D INFO] Set WEBRTC_STUN_SERVER environment variable add a customized WebRTC STUN server.
[Open3D INFO] WebRTC Jupyter handshake mode enabled.
